# Autocorrelation II

In this notebook we are going to commit ourselves to the study of the autocorrelation function. In particular we are going to apply the autocorrelation to the Lorenz system and an autoregression (AR) process.

In [3]:
from plotly import offline as py
from plotly import graph_objs as go

py.init_notebook_mode(connected=True)

from dynamics import lorenz_rk4
from dynamics import autoregression

We define the AR process as map,
$$
x_{n+1}=a + bx_n+\eta,
$$
wherein $a,b\in\mathbb{R}$ are constant system parameters and $\eta$ is sampled from $\mathcal{N}(0,1)$. 

In [48]:
x1, _, _ = lorenz_rk4(5.3, 3.0, 3.0, 10, 100, 8/3, 5000, 0.005)
x2, _, _ = lorenz_rk4(5.3, 3.0, 3.0, 10, 28, 8/3, 5000, 0.005)
x3 = autoregression(1.0, 0.0, 0.9, 5000)

In [50]:
data = [
    go.Scatter(y=x1, name='Lorenz (b = 100)'),
    go.Scatter(y=x2, name='Lorenz (b = 28)'),
    go.Scatter(y=x3, name='AR (c = 0.9)')
]

figure = go.Figure(data=data, layout=go.Layout(
    title='Time series',
    showlegend=True,
    xaxis=dict(title='n'),
    yaxis=dict(title='x_n')
))

py.iplot(figure)

The AR process is dominated by noise. Both Lorenz time series show different behaviour with the Lorenz system with $b=100$ appearing more periodic.

In [73]:
def autocor_direct(x):
    a = np.correlate(x, x, mode='full')

    return a[a.size // 2:]

def autocor_fourier(x):
    X = np.fft.fft(x)
    P = np.abs(X)**2
    a = np.fft.ifft(P)
    
    return a.real

We implemented the autocorrelation function via the direct calculation and through the inverse Fourier transform of the power spectrum (Wiener-Khinchin).

In [74]:
a1 = autocor_direct(x1)
a2 = autocor_direct(x2)
a3 = autocor_direct(x3)

data = [
    go.Scatter(y=a1, name='Lorenz (b = 100)'),
    go.Scatter(y=a2, name='Lorenz (b = 28)'),
    go.Scatter(y=a3, name='AR (c = 0.9)')
]

figure = go.Figure(data=data, layout=go.Layout(
    title='Autocorrelation',
    showlegend=True,
    xaxis=dict(title='𝜏'),
    yaxis=dict(title='<x(t)x(t+𝜏)>')
))

py.iplot(figure)

In [75]:
b1 = autocor_fourier(x1)
b2 = autocor_fourier(x2)
b3 = autocor_fourier(x3)

data = [
    go.Scatter(y=a1, name='Direct'),
    go.Scatter(y=b1, name='Fourier')
]

figure = go.Figure(data=data, layout=go.Layout(
    title='Lorenz (b = 100)',
    showlegend=True,
    xaxis=dict(title='𝜏'),
    yaxis=dict(title='<x(t)x(t+𝜏)>')
))

py.iplot(figure)

In [76]:
data = [
    go.Scatter(y=a2, name='Direct'),
    go.Scatter(y=b2, name='Fourier')
]

figure = go.Figure(data=data, layout=go.Layout(
    title='Lorenz (b = 28)',
    showlegend=True,
    xaxis=dict(title='𝜏'),
    yaxis=dict(title='<x(t)x(t+𝜏)>')
))

py.iplot(figure)

In [77]:
data = [
    go.Scatter(y=a3, name='Direct'),
    go.Scatter(y=b3, name='Fourier')
]

figure = go.Figure(data=data, layout=go.Layout(
    title='Autoregression (c = 0.9)',
    showlegend=True,
    xaxis=dict(title='𝜏'),
    yaxis=dict(title='<x(t)x(t+𝜏)>')
))

py.iplot(figure)

The Wiener-Khinchin theorem seems to hold for small $\tau$ on the Lorenz system. We observe some symmetry in the autocorrelation function obtained from the Fourier transform. Probably it is possible to capture important characteristics of the autocorrelation function obtained by direct calculation for greater $\tau$ if one has higher sampling rate.

In [78]:
data = [
    go.Scatter(y=x1 + x3, name='Lorenz + AR (b = 100)'),
    go.Scatter(y=x2 + x3, name='Lorenz + AR (b = 28)'),
]

figure = go.Figure(data=data, layout=go.Layout(
    title='Time series',
    showlegend=True,
    xaxis=dict(title='n'),
    yaxis=dict(title='x_n')
))

py.iplot(figure)

The superposition of the time series of the $x$ coordinates of the Lorenz system and the noise dominated AR process appear like noisy versions of the pure time series. Because the time series corresponding to $b=100$ has greater amplitude the noise does not look as dominant as in the case of the superposition with $b=28$ time series.

In [83]:
a13 = autocor_direct(x1 + x3)

data = [
    go.Scatter(y=a1, name='Lorenz (b = 100)'),
    go.Scatter(y=a3, name='AR (c = 0.9)'),
    go.Scatter(y=a13, name='Lorenz + AR'),
]

figure = go.Figure(data=data, layout=go.Layout(
    title='Autocorrelation',
    showlegend=True,
    xaxis=dict(title='𝜏'),
    yaxis=dict(title='<x(t)x(t+𝜏)>')
))

py.iplot(figure)

The autocorrelation of the superposition matches exactly the autocorrelation of the undisturbed Lorenz system.

In [80]:
b13 = autocor_fourier(x1 + x3)

data = [
    go.Scatter(y=a13, name='Direct'),
    go.Scatter(y=b13, name='Fourier'),
]

figure = go.Figure(data=data, layout=go.Layout(
    title='Autocorrelation',
    showlegend=True,
    xaxis=dict(title='𝜏'),
    yaxis=dict(title='<x(t)x(t+𝜏)>')
))

py.iplot(figure)

There is nothing new compared to the undisturbed case to see.

In [82]:
a23 = autocor_direct(x2 + x3)

data = [
    go.Scatter(y=a1, name='Lorenz (b = 28)'),
    go.Scatter(y=a3, name='AR (c = 0.9)'),
    go.Scatter(y=a13, name='Lorenz + AR'),
]

figure = go.Figure(data=data, layout=go.Layout(
    title='Autocorrelation',
    showlegend=True,
    xaxis=dict(title='𝜏'),
    yaxis=dict(title='<x(t)x(t+𝜏)>')
))

py.iplot(figure)

Again the noise seems to be not present in the autocorrelation of the superposition.

#### Summary

In opposition to pure white nosie the AR process seems to be filtered out by the autocorrelation function, thus, the autocorrelation function appears invariant unter superpositions of AR processes.

Furthermore the Wiener-Khinchin theorem seems to hold sufficiently to capture the global characteristics of the true autocorrelation function for small $\tau$. For greater $\tau$ the autocorrelation function obtained from the power spectrum shows deviations from the true autocorrelation function.